In [2]:
import os
from selenium import webdriver
import pickle
from bs4 import BeautifulSoup
from library.utilities import *
import pandas as pd

In [3]:
# cnn_transcripts = get_cnn_text(df_cnn, 'data/transcripts/transcripts_cnn.pickle')
cnn_transcripts = get_pickle('data/transcripts/transcripts_cnn.pickle')
cnn_transcripts[:5]

[['(COMMERCIAL BREAK)',
  '',
  "[21:00:35] ANDERSON COOPER, AC360 HOST:  Hey good evening.  Thanks for joining us 9:00 P.M., in New York, where we have breaking news.  New polling that will not be welcome news for Hillary Clinton, it is 6:00 P.M., the Reagan Library in Simi Valley, Southern California, site of next week's CNN Republican Presidential Debate.  Now just six days away, the breaking news on that, we can now say that these are the 11 candidates who qualify for the main debate.  Rand Paul, Huckabee, Marco Rubio, Ted Cruz, Dr. Ben Carson, Donald Trump, Jeb Bush, Scott Walker, Carly Fiorina, John Kasick, and Chris Christie.",
  '',
  "Five others will be debating earlier and here are the republican leaders in our new CNN/ORC polling with Donald Trump now topping 30 percent for the very first time.  Dr. Carson is the only other candidate in double digits, so he very busy hour ahead, a lot to talk about starting on the democratic side where those new CNN/ORC poll numbers have ju

In [52]:

url = 'http://transcripts.cnn.com/TRANSCRIPTS/1608/10/acd.01.html'

def get_soup(url):
    f = urlopen(url)
    f.geturl()
    return BeautifulSoup(f.read(), 'lxml')

def soup_to_list(soup):
    a_list = [x.encode('utf-8').strip() for x in soup.body.prettify().split('<br/>\n')]
    a_list = [x for x in a_list if '<body id' not in x]
    return a_list

def rid_times(l):
    return_list = []
    for s in l:
        try:
            m = re.search(r"\[([A-Za-z0-9_]+):([A-Za-z0-9_]+):([A-Za-z0-9_]+)\]", s)
            s_rid = m.group(0)
            s_new = s.replace(s_rid, '')
            return_list.append(s_new)
        except:
            return_list.append(s)
    return return_list

def rid_parentheses(a_list):
    return_list = []
    replace_pattern = r'(?<=\()(.*?)(?=\))'
    for element in a_list:
        try:
            target = '(' + re.findall(replace_pattern, element)[0] + ')'
            replacement_element = element.replace(target, '')
            return_list.append(replacement_element)
            
        except:
            return_list.append(element)
    return return_list

    
def rid_tags(a_list):
    return [x for x in a_list if '<' not in x]

def rid_backslashes(a_list):
    return_list = []
    for string in a_list:
        new_string = string.replace("\\", "")
        return_list.append(new_string)
    return return_list


def rid_empty_strings(a_list):
    return [x for x in a_list if len(x) > 0]

        


soup = get_soup(url)
a_list = soup_to_list(soup)
list_cleaned = rid_times(a_list)
list_cleaned = rid_parentheses(list_cleaned)
list_cleaned = rid_tags(list_cleaned)
list_cleaned = rid_backslashes(list_cleaned)
list_cleaned = rid_backslashes(list_cleaned)
list_cleaned = replace_colons_in_times(list_cleaned)
list_cleaned = rid_empty_strings(list_cleaned)
list_cleaned = [x.lstrip() for x in list_cleaned]
list_cleaned

['JOHN BERMAN, CNN ANCHOR:  Good evening.  John Berman here, in for Anderson.',
 "It was about the only thing missing in this campaign, a man with suction cups climbing a building, about 20 stories up Trump Tower. That's about how far this guy got, suction cups and all before members of the NYPD's elite emergency services unit grabbed him as stunned people on the street looked on.",
 "This climbing standoff just one of several campaign stories any one of which could lead the newscast and we'll get to all of it.",
 'First, New York authorities just briefed on what went down and who went up.  Listen to the officer who pulled the climber in.',
 'POLICE OFFICER:  I was waiting for the perfect time to present itself. When I felt it was safe for him and myself and my crew so when that time came and I did talk to my crew and let them know, listen, he\'s at a level where I am able to grab him safely and bring him in.  When it presented itself, I reached out, I took hold of his hand and I said,

In [76]:
def list_to_list_of_pairs(l):
    """
    returns pair of strings for each input list element
    """
    return_list = []
    for s in l:
        
        l_pair = [x for x in s.split(':',1)]
        if len(l_pair) == 1:
            l_pair = ['ADD NAME'] + l
        return_list.append(l_pair)
    return return_list
list_to_list_of_pairs(list_cleaned)

[['JOHN BERMAN, CNN ANCHOR',
  '  Good evening.  John Berman here, in for Anderson.'],
 ['ADD NAME',
  'JOHN BERMAN, CNN ANCHOR:  Good evening.  John Berman here, in for Anderson.',
  "It was about the only thing missing in this campaign, a man with suction cups climbing a building, about 20 stories up Trump Tower. That's about how far this guy got, suction cups and all before members of the NYPD's elite emergency services unit grabbed him as stunned people on the street looked on.",
  "This climbing standoff just one of several campaign stories any one of which could lead the newscast and we'll get to all of it.",
  'First, New York authorities just briefed on what went down and who went up.  Listen to the officer who pulled the climber in.',
  'POLICE OFFICER:  I was waiting for the perfect time to present itself. When I felt it was safe for him and myself and my crew so when that time came and I did talk to my crew and let them know, listen, he\'s at a level where I am able to grab 

In [94]:
def string_to_list(s):
    l_pair = [x for x in s.split(':',1)]
    if len(l_pair) == 1:
        l_pair = ['ADD NAME'] + l_pair
    return l_pair

def get_names_and_text(l):
    names = []
    text = []
    for s in l:
        pair = string_to_list(s)
        names.append(pair[0])
        text.append(pair[1])
    return names, text

In [102]:
names, text = get_names_and_text(list_cleaned)

In [109]:
from copy import deepcopy

def replace_empty_names(names):
    names_2 = deepcopy(names)
    for idx, name in enumerate(names):
        if name == 'ADD NAME':
            names_2[idx] = names_2[idx-1]
        else:
            names_2[idx] = name
    return names_2

In [110]:
replace_empty_names(names)

['JOHN BERMAN, CNN ANCHOR',
 'JOHN BERMAN, CNN ANCHOR',
 'JOHN BERMAN, CNN ANCHOR',
 'JOHN BERMAN, CNN ANCHOR',
 'POLICE OFFICER',
 'BERMAN',
 'BERMAN',
 'BERMAN',
 'BERMAN',
 'BRYNN GINGRAS, CNN CORRESPONDENT',
 'BRYNN GINGRAS, CNN CORRESPONDENT',
 'BRYNN GINGRAS, CNN CORRESPONDENT',
 'BRYNN GINGRAS, CNN CORRESPONDENT',
 'GINGRAS ',
 'GINGRAS ',
 'GINGRAS ',
 'GINGRAS ',
 'GINGRAS ',
 'GINGRAS ',
 'GINGRAS ',
 'GINGRAS ',
 'GINGRAS',
 'GINGRAS',
 'BERMAN',
 'BERMAN',
 'BERMAN',
 'BERMAN',
 'SHIMON PROKUPECZ, CNN LAW ENFORCEMENT PRODUCER',
 'SHIMON PROKUPECZ, CNN LAW ENFORCEMENT PRODUCER',
 'SHIMON PROKUPECZ, CNN LAW ENFORCEMENT PRODUCER',
 'SHIMON PROKUPECZ, CNN LAW ENFORCEMENT PRODUCER',
 'BERMAN',
 'BERMAN',
 'PROKUPECZ',
 'PROKUPECZ',
 'PROKUPECZ',
 'BERMAN',
 'PAUL CALLAN, CNN LEGAL ANALYST',
 'PAUL CALLAN, CNN LEGAL ANALYST',
 'PAUL CALLAN, CNN LEGAL ANALYST',
 'BERMAN',
 'BERMAN',
 'CHRISTINE QUINN, FORMER NYC CITY COUNCIL SPEAKER',
 'CHRISTINE QUINN, FORMER NYC CITY COUNCIL SPE

In [73]:
return_list = []
for i in list_cleaned:
    
    return_list.append(split_names_from_text(i))

In [74]:
return_list

[['JOHN BERMAN, CNN ANCHOR',
  '  Good evening.  John Berman here, in for Anderson.'],
 ['ADD NAME',
  "It was about the only thing missing in this campaign, a man with suction cups climbing a building, about 20 stories up Trump Tower. That's about how far this guy got, suction cups and all before members of the NYPD's elite emergency services unit grabbed him as stunned people on the street looked on."],
 ['ADD NAME',
  "This climbing standoff just one of several campaign stories any one of which could lead the newscast and we'll get to all of it."],
 ['ADD NAME',
  'First, New York authorities just briefed on what went down and who went up.  Listen to the officer who pulled the climber in.'],
 ['POLICE OFFICER',
  '  I was waiting for the perfect time to present itself. When I felt it was safe for him and myself and my crew so when that time came and I did talk to my crew and let them know, listen, he\'s at a level where I am able to grab him safely and bring him in.  When it present

In [37]:
import re

def rid_times(s):
    try:
        m = re.search(r"\[([A-Za-z0-9_]+):([A-Za-z0-9_]+):([A-Za-z0-9_]+)\]", s)
        s_rid = m.group(0)
        return s.replace(s_rid, '')
    except:
        return s

In [38]:
cnn_transcripts[0][2]
rid_brackets(cnn_transcripts[0][2])
#rid_brackets('d[f:f]')

" ANDERSON COOPER, AC360 HOST:  Hey good evening.  Thanks for joining us 9:00 P.M., in New York, where we have breaking news.  New polling that will not be welcome news for Hillary Clinton, it is 6:00 P.M., the Reagan Library in Simi Valley, Southern California, site of next week's CNN Republican Presidential Debate.  Now just six days away, the breaking news on that, we can now say that these are the 11 candidates who qualify for the main debate.  Rand Paul, Huckabee, Marco Rubio, Ted Cruz, Dr. Ben Carson, Donald Trump, Jeb Bush, Scott Walker, Carly Fiorina, John Kasick, and Chris Christie."

In [236]:
# cnn_transcripts = get_cnn_text(df_cnn, 'data/transcripts/transcripts_cnn.pickle')
cnn_transcripts = get_pickle('data/transcripts/transcripts_cnn.pickle')
cnn_transcripts[:5]

['JOHN BERMAN, CNN ANCHOR:  Good evening.  John Berman here, in for Anderson.',
 "It was about the only thing missing in this campaign, a man with suction cups climbing a building, about 20 stories up Trump Tower. That's about how far this guy got, suction cups and all before members of the NYPD's elite emergency services unit grabbed him as stunned people on the street looked on.",
 "This climbing standoff just one of several campaign stories any one of which could lead the newscast and we'll get to all of it.",
 'First, New York authorities just briefed on what went down and who went up.  Listen to the officer who pulled the climber in.',
 'POLICE OFFICER:  I was waiting for the perfect time to present itself. When I felt it was safe for him and myself and my crew so when that time came and I did talk to my crew and let them know, listen, he\'s at a level where I am able to grab him safely and bring him in.  When it presented itself, I reached out, I took hold of his hand and I said,

In [255]:
# cnn cleaning functions

speaker_name = []
speaker_text = []
for idx, string in enumerate(list_cleaned):
    if ':' in string:
        name = string.split(':')[0].rstrip()
        text = string.replace(name + ':', '').lstrip()
        speaker_name.append(name)
        speaker_text.append(text)
    else:
        name = 'ADD NAME'
        text = string.lstrip()
        speaker_name.append(name)
        speaker_text.append(text)
speaker_name_text_1 = zip(speaker_name, speaker_text)

import copy
speaker_name_text_2 = copy.copy(speaker_name_text_1)
speaker_name_text_2 = [list(x) for x in speaker_name_text_2]

In [259]:
for idx, i in enumerate(speaker_name_text_1):
    if i[0] == 'ADD NAME':
        speaker_name_text_2[idx][0] = speaker_name_text_2[idx-1][0]
speaker_name_text_2

[['JOHN BERMAN, CNN ANCHOR',
  'Good evening.  John Berman here, in for Anderson.'],
 ['JOHN BERMAN, CNN ANCHOR',
  "It was about the only thing missing in this campaign, a man with suction cups climbing a building, about 20 stories up Trump Tower. That's about how far this guy got, suction cups and all before members of the NYPD's elite emergency services unit grabbed him as stunned people on the street looked on."],
 ['JOHN BERMAN, CNN ANCHOR',
  "This climbing standoff just one of several campaign stories any one of which could lead the newscast and we'll get to all of it."],
 ['JOHN BERMAN, CNN ANCHOR',
  'First, New York authorities just briefed on what went down and who went up.  Listen to the officer who pulled the climber in.'],
 ['POLICE OFFICER',
  'I was waiting for the perfect time to present itself. When I felt it was safe for him and myself and my crew so when that time came and I did talk to my crew and let them know, listen, he\'s at a level where I am able to grab him 

In [144]:
speaker_2 = []
text_2 = []
for idx, a_tuple in enumerate(speaker_name_text_1):
    
    if a_tuple[0] == 'ADD NAME' and idx ==0:
        speaker == 'UNKNOWN'
    elif a_tuple[0] == 'ADD NAME':
        speaker = speaker_name_text[idx-1][0]
    else:
        speaker = a_tuple[0]
    speaker_2.append(speaker)
        


<!DOCTYPE html>\n<html lang="en">\n<head>\n<meta content="text/html; charset=unicode-escape" http-equiv="content-type"/>\n<title>CNN.com - Transcripts</title>\n<link href="http://i.cnn.net/cnn/.element/ssi/css/1.3/story.css" rel="stylesheet" type="text/css"/>\n<script language="JavaScript1.1" src="http://i.cnn.net/cnn/.element/ssi/js/1.3/main.js" type="text/javascript"></script>\n<script>\n\tvar cnnSiteWideCurrDate = new Date(2013, 1, 12);\n</script>\n<style type="text/css">\n<!--\n.cnnTransHeaders,\n.cnnTransDate\n{ font-family: verdana, arial, sans-serif; }\n\n.cnnTransCal,\n.cnnTransHead,\n.cnnTransStoryHead,\n.cnnTransSubHead\n{ font-family: arial, helvetica, sans-serif; }\n\n.cnnTransHeaders,\n.cnnTransDate,\n.cnnTransProv\n{ font-size: 10px; }\n\n.cnnTransSubHead\n{ font-size: 12px; }\n\n.cnnTransHead\n{ font-size: 14px; }\n\n.cnnTransStoryHead\n{ font-size: 16px; }\n\n.cnnTransHeaders,\n.cnnTransDate,\n.cnnTransHead,\n.cnnTransStoryHead,\n.cnnTransSubHead,\n.cnnTransProv\n{ font

In [93]:
test = '[bc]'
pattern = r'^\[.*\]'
compiled = re.compile(pattern)
ms = compiled.sub(test, 'a')

In [101]:
list_cleaned = [x.split(']') for x in list_cleaned if ']' in x]

In [102]:
list_cleaned

[]